# Fitting of $F_{res} vs. H$  for pMTJ structures using Python

##Introduction

In this project, we ae going to model an all prependicular device based on Kittle formula and try to calculate its FMR frequency under the application of a tilted field.
The structure contains two magnetic layers, $1$ is the fixed layer and $2$ is the free layer, which are separated by an insulator spacer. Based on Kittle formula, the resonance frequency, $\omega_r$, for an applied DC magnetic field, $H_{dc}$, is equal to

$\displaystyle(\frac{\omega_r}{\gamma})^2=H_1 H_2$

$\left\{
    \begin{array}{ll}
        \displaystyle H_1=H_{dc}\ cos(θ_H−θ_2)+H_{st}\ cos(θ_2−θ_1)−H_{K21}^{eff}\ cos^2θ_2−H_{K22}\ cos^4θ_2 \\
        \displaystyle H_2=H_{dc}\ cos(θ_H-θ_2)+H_{st}\ cos(θ_2−θ_1)−(H_{K21}^{eff}+\frac{H_{K22}}{2})\ cos2θ_2−\frac{H_{K22}}{2}\ cos 4θ_2
    \end{array}
\right.$


Here, $\gamma$ is Gyromagnetic ratio, $\displaystyle H_{Ki1}^{eff} = \frac{M_s}{\mu_0} - 2*\frac{K_{i1}+2K_{i2}}{M_s}$ and $\displaystyle H_{Ki2}^{eff} = 4*\frac{K_{i2}}{M_s} $ are the magnetic anisotropy fields in which $K_{i1}$ and $K_{i2}$ are the first and second order anisotropy for the $i_{th}$ layer. $H_{st}$ is defined as the stray field between the layers. $θ_H$ is the angle of the DC applied field and $θ_1$ and $θ_2$ are the equilibrium angles of the layers when the DC field is applied to the structure. All the angles are defined w.r.t. the normal vector of the layers. To find $θ_1$ and $θ_2$ values, the equilibrium conditions of both the layers should be solved for all the applied field values. 

$H_{dc}\ sin(θ_H − θ_{eq1})−H_{st}\ sin(θ_{eq1}−θ_{eq2})+H_{K11}^{eff}\ sinθ_{eq1}\ cosθ_{eq1}+H_{K12}\ sinθ_{eq1}\ cos^3θ_{eq1}=0$

$H_{dc}\ sin(θ_H − θ_{eq2})−H_{st}\ sin(θ_{eq2}−θ_{eq1})+H_{K21}^{eff}\ sinθ_{eq2}\ cosθ_{eq2}+H_{K22}\ sinθ_{eq2}\ cos^3θ_{eq2}=0$

![pMTJ Structure](Schematics/Structure.PNG "pMTJ Structure")

In order to simplify the model, we consider the fixed layer is always prependicular ($θ_{eq1} = 0$), and also ignore the second order anisotropy of the free layer ($H_{K22} = 0$). Then the equilibrium condition for the free layer is: 

$H_{dc}\ sin(θ_H − θ_{eq2})−H_{st}\ sin(θ_{eq2})+H_{K21}^{eff}\ sinθ_{eq2}\ cosθ_{eq2}=0$


Also $H_{1}$ and $H_{2}$ is simpliefied to 

$\left\{
    \begin{array}{ll}
        \displaystyle H_1=H_{dc}\ cos(θ_H−θ_2)+H_{st}\ cos(θ_2)−H_{K21}^{eff}\ cos^2θ_2 \\
        \displaystyle H_2=H_{dc}\ cos(θ_H-θ_2)+H_{st}\ cos(θ_2)−(H_{K21}^{eff})\ cos2θ_2
    \end{array}
\right.$

Using the formula, we can simply extract the equilibrium angle of the magnetization versus the strength of the field for a given external field angel.

##Results

First we import the $Python$ libraries we need. $Numpy$ for handling arrays, $Scipy$ for finding the equilibrium angle, and $pylab$ for plotting.

In [1]:
from scipy.optimize import fsolve
import math
import numpy as np
from scipy.optimize import curve_fit
from numpy import *
import matplotlib.pyplot as plt
import matplotlib.lines as mlines

import pylab as pl           # Imports all plotting capability of magplotlib.
%matplotlib inline           
# "%matplotlib inline" makes all plots show up inside the document (i.e. "inline") and not in a separate plot window.

Then we need to set the ranges for the parameters in our model.
Here we can define the ranges for $H_{K11}$ and $Hst$. The code uses for loops to solve the equation for every combinations of these two parameters.

In [2]:
Hk21max=16000
Hk21min=16000
Hk21step=500 # should be positive
#----------------------------------
Hstmax=0
Hstmin=0
Hststep=500 # should be positive
#==================================
gamma = 0.00319

Here, the external field is defined.
$angle$ is the angle of the applied DC magnetic field in degree w.r.t. the normal vector of the layers (For in-plane field, $angle = 90$), and $H_{dc}$ is vector contains the strength of the applied field.

In [3]:
angle=20

#Whole the range
Hdc = array(range(0, 20000, 50))

Here the equilibrium condition and the resonance frequency for the free layer based on Kittel formula are defined.

In [4]:
def equilibrium_eq(p):
    theta2 = p
    return (H*math.cos(theta2+np.pi/2-thetaH)-Hst*math.sin(theta2)+Hk21*math.sin(theta2)*math.cos(theta2))
################################################################################
def fres_func(Hdc, theta2):
    return gamma*( (Hdc*np.sin(theta2+np.pi/2-thetaH)+Hst*np.cos(theta2)-(HK21)*np.cos(2*theta2)) * (Hdc*np.sin(theta2+np.pi/2-thetaH)+Hst*np.cos(theta2)-HK21*np.cos(theta2)**2) )**(0.5)


The next cell is for the initialization of the variables used in the code.

In [5]:
thetaH=np.pi/180*(angle)
Theta2 = array(zeros(len(Hdc)))
Frequency = array(zeros(len(Hdc)))



Here, based on the ranges defined for the parameters, the code does the sweep and fitting. The output is the table contains the combination of the parameters and the calculated $adj.r.sq$ values.

In [6]:
print "=========================================================================================================================="
print "----------------------------------------------------------------------------"
print "gamma=",gamma,", angle=",angle
print "Hdc :", (Hdc)
print "----------------------------------------------------------------------------"
plt.close('all')
print "=========================================================================================================================="
for Hst in xrange(Hstmin,Hstmax+Hststep,Hststep):
    for Hk21 in xrange(Hk21min,Hk21max+Hk21step,Hk21step):
        HK21=[Hk21]
        for i in xrange(0,len(Hdc)):
            H = Hdc[i]
            x2 =  fsolve(equilibrium_eq, (0))
            Theta2[i]=x2
################################################################################
        Frequency = fres_func(Hdc, Theta2)
        print "Hst=",np.round(Hst),", Hk21=",np.round(Hk21)
        print "--------------------------------------------------------------------------------------------------------------------------"
        print "theta :", (Theta2/np.pi*180)
        print "=========================================================================================================================="
        print "--------------------------------------------------------------------------------------------------------------------------"
        print "Frequency :", (Frequency)
        print "=========================================================================================================================="
        plt.figure("Theta", figsize=(8, 6), dpi=80)
        plt.ylabel('theta (degree)')
        plt.xlabel('Hdc (Oe)')
        plt.plot(Hdc, Theta2/np.pi*180)
        #plt.plot(Hdc,  angel, 'g^',label='Field angle')
        #plt.title('Theta1:blue, Theta2:red, Relative Theta:green ')
        #plt.legend(loc='upper left',handles=[mlines.Line2D([], [], color='blue', marker='s', label='Theta1'),mlines.Line2D([], [], color='red', marker='s', label='Theta2'),mlines.Line2D([], [], color='green', marker='^', label='relTheta')],numpoints=1)       
        plt.figure("main", figsize=(8, 6), dpi=80)
        ax = plt.subplot(111)
        plt.ylabel('f_resonance (GHz)')
        plt.xlabel('Hdc (Oe)')
        plt.plot(Hdc, Frequency)
        #plt.plot(Hdc, fittedFres, label=('Hk21='+str(Hk21)+' ,Hst='+str(Hst)) )
            


----------------------------------------------------------------------------
gamma= 0.00319 , angle= 20
Hdc : [    0    50   100   150   200   250   300   350   400   450   500   550
   600   650   700   750   800   850   900   950  1000  1050  1100  1150
  1200  1250  1300  1350  1400  1450  1500  1550  1600  1650  1700  1750
  1800  1850  1900  1950  2000  2050  2100  2150  2200  2250  2300  2350
  2400  2450  2500  2550  2600  2650  2700  2750  2800  2850  2900  2950
  3000  3050  3100  3150  3200  3250  3300  3350  3400  3450  3500  3550
  3600  3650  3700  3750  3800  3850  3900  3950  4000  4050  4100  4150
  4200  4250  4300  4350  4400  4450  4500  4550  4600  4650  4700  4750
  4800  4850  4900  4950  5000  5050  5100  5150  5200  5250  5300  5350
  5400  5450  5500  5550  5600  5650  5700  5750  5800  5850  5900  5950
  6000  6050  6100  6150  6200  6250  6300  6350  6400  6450  6500  6550
  6600  6650  6700  6750  6800  6850  6900  6950  7000  7050  7100  7150
  7200  7250  

/ext/sage/sage-8.0/local/lib/python2.7/site-packages/scipy/optimize/minpack.py:161: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.
  warnings.warn(msg, RuntimeWarning)
/ext/sage/sage-8.0/local/lib/python2.7/site-packages/scipy/optimize/minpack.py:161: RuntimeWarning: The iteration is not making good progress, as measured by the 
  improvement from the last five Jacobian evaluations.
  warnings.warn(msg, RuntimeWarning)
/ext/sage/sage-8.0/local/lib/python2.7/site-packages/ipykernel/__main__.py:6: RuntimeWarning: invalid value encountered in sqrt


[  0.          -0.06141884  -0.1232006   -0.18534859  -0.24786615
  -0.31075667  -0.37402359  -0.43767038  -0.50170059  -0.56611778
  -0.63092559  -0.69612768  -0.7617278   -0.82772971  -0.89413724
  -0.96095429  -1.02818479  -1.09583274  -1.16390219  -1.23239726
  -1.30132212  -1.37068099  -1.44047818  -1.51071804  -1.58140499
  -1.65254352  -1.72413818  -1.79619361  -1.86871449  -1.94170559
  -2.01517175  -2.08911789  -2.16354899  -2.23847013  -2.31388645
  -2.38980319  -2.46622566  -2.54315926  -2.62060949  -2.69858191
  -2.7770822   -2.85611613  -2.93568956  -3.01580843  -3.09647882
  -3.17770689  -3.2594989   -3.34186123  -3.42480038  -3.50832294
  -3.59243563  -3.6771453   -3.7624589   -3.84838353  -3.9349264
  -4.02209486  -4.10989641  -4.19833866  -4.28742939  -4.37717652
  -4.46758812  -4.55867241  -4.65043778  -4.74289278  -4.83604614
  -4.92990675  -5.02448368  -5.11978619  -5.21582374  -5.31260597
  -5.41014272  -5.50844405  -5.60752024  -5.70738176  -5.80803934
  -5.909503

/ext/sage/sage-8.0/local/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')
